# Ознакомление с заданием

Полное описание кейсового задания:

На основе больших данных о предыдущем опыте взаимодействия с клиентами разработать модель, позволяющую прогнозировать вероятность покупки клиентами дополнительных услуг в частности, приобретения машиномест в паркинге.
Среди клиентов компании - владельцев квартир необходимо выделить покупателей, наиболее склонных к покупке машиноместа. С такими клиентами будет проводиться коммуникация (смс, эл. письмо) с предложением приобрести машиноместо.
Входные данные представляют собой наборы признаков по клиентам на первое число каждого месяца за 1,5 года (sample данных).
Целевой признак равен 1, если в следующие 3 месяцев клиент купит машиноместо. После покупки машиноместа клиент исключается из наборов данных.
Результатом предсказания модели должен стать скор (значение от 0 до 1) по каждому клиенту - вероятность, что клиент купит машиноместо в следующие 3 месяцев.
Оцениваться результат будет метрикой ROC-AUC.

Есть колонки report_date (дата среза признаков) и client_id (уникальный идентификатор клиента).  Названия остальных колонок зашифрованы и представляют собой признаковое пространство для скоринга.

Среди признаков по клиенту представлены такие признаки как:
- история взаимодействия клиента с сайтом компании за разные периоды времени: просмотры, клики, заполнение форм обратной связи и т.п.
- интересы клиента, выявленные в ходе общения с клиентом
- история входящих и исходящих звонков по клиенту
- история встреч с клиентом
- избранные объекты недвижимости клиента
- имеющиеся договора клиента
- характеристики имеющихся ипотечных заявок
- вероятность наличия у клиента авто
Так как не все клиенты проходят через этап сайта, звонка, встречи, брони датасет получается разряженным - это специфика взаимодействия с клиентом. 


Необходимо иметь ввиду, что мы имеем дело с панельными данными - по каждому клиенту в датасете могут быть представлены несколько срезов за разные даты.
И в обучающем, и в тестовом датасете представлены не полные данные, а только подвыборки из ген совокупности.
При моделировании рекомендуется использовать кросс-валидацию.

Исходя из задания делаю некоторые преждевременные заметки:
- предоставлены данные о предыдущем опыте взаимодействия с клиентами, также стоит учесть что каждому клиенту в датасете может быть представлено несколько срезов за разные даты.
- в данном случае требуется использовать модель бинарной классификации

# Чтение файла и вывод основной информации
импорт библиотек и файла, знакомство с датасетом

In [1]:
import pandas as pd
import numpy as np

import matplotlib.pyplot as plt
import seaborn as sns

In [2]:
df = pd.read_csv('train.csv').drop_duplicates() #загружаю датасет в переменную, сразу убирая дубликаты
df.head()

C:\Users\Илья\AppData\Local\Temp\ipykernel_19088\2509017205.py:1: DtypeWarning: Columns (51,52,53,54,55,56,57,58,59,60,61,62,63,64,65,66,87,88,89,90,91,92,93,94,95,96,97,98,99,100,101,102,131,132,133,135,136,139,140,141,142,143,144,145,146,147,148,149,151,152,155,156,157,158,159,160,161,163,164,165,167,168,169,171,172,173,174,175,176,177,178,183,184,185,186,187,188,189,190,191,192,193,194,195,196,197,198,203,204,205,206,207,208,209,210,211,212,213,214,215,216,217,218,223,224,227,239,240,241,242,243,244,245,246,459,460,461,467,468,469,515,516,523,524,531,532,539,540,547,548,555,556,563,564,565,567,571,572,573,575,579,580,581,582,583,587,588,595,596,603,604,611,612,613,615,795,796,797,799,1031,1032,1033,1034,1035,1036,1037,1039,1040,1041,1042,1043,1044,1045,1047,1048,1049,1050,1051,1052,1055,1056,1057,1058,1059,1060,1063,1064,1065,1067,1068,1069,1072,1073,1074,1075,1076,1077,1078,1172,1173,1174,1176,1177,1178,1179,1180,1181,1182,1275,1276,1277,1278,1279,1280,1281,1282,1447,1448,1449,1450

report_date  client_id  target  col1  col2  col3  col4  col5  col6  col7  \
0  2022-11-01          1       0   NaN   NaN   NaN   NaN   NaN   NaN   NaN   
1  2022-11-01          5       0   NaN   NaN   NaN   NaN   NaN   NaN   NaN   
2  2022-05-01          6       0   NaN   NaN   NaN   NaN   NaN   NaN   NaN   
3  2022-09-01          7       0   NaN   NaN   NaN   NaN   NaN   NaN   NaN   
4  2022-08-01          8       0   NaN   NaN   NaN   NaN   NaN   NaN   NaN   

   ...    col2654    col2655    col2656  col2657  col2658  col2659    col2660  \
0  ...        NaN        NaN        NaN      NaN      NaN      NaN        NaN   
1  ...  7616803.0  7616803.0  7616803.0      NaN      NaN      NaN  7616803.0   
2  ...        NaN        NaN        NaN      NaN      NaN      NaN        NaN   
3  ...        NaN        NaN        NaN      NaN      NaN      NaN        NaN   
4  ...        NaN        NaN        NaN      NaN      NaN      NaN        NaN   

     col2661    col2662   col2663  
0        NaN        NaN  0.256261  
1  7616803.0  7616803.0  0.256261  
2        NaN        NaN  0.256261  
3        NaN        NaN  0.258682  
4        NaN        NaN  0.254164  

[5 rows x 2666 columns]

In [3]:
# Вывожу размерность датасета
df.shape

(14456, 2666)

In [4]:
# Вывожу уникальные значения в каждой колонке, 
for column in df.columns:
    unique_values = df[column].unique().tolist()
    print(f"Уникальные значения в колонке '{column}': {unique_values}")


Уникальные значения в колонке 'report_date': ['2022-11-01', '2022-05-01', '2022-09-01', '2022-08-01', '2023-02-01', '2023-01-01', '2022-02-01', '2022-12-01', '2022-06-01', '2022-10-01', '2021-08-01', '2021-05-01', '2022-04-01', '2022-03-01', '2022-07-01', '2021-10-01', '2021-02-01', '2022-01-01', '2021-12-01', '2021-04-01', '2021-06-01', '2021-11-01', '2021-07-01', '2021-09-01', '2021-03-01']
Уникальные значения в колонке 'client_id': [1, 5, 6, 7, 8, 10, 16, 17, 18, 19, 21, 22, 23, 24, 25, 26, 27, 28, 30, 31, 32, 33, 34, 35, 36, 37, 38, 39, 40, 42, 43, 44, 45, 46, 47, 48, 49, 50, 51, 52, 53, 54, 55, 57, 59, 64, 66, 67, 68, 69, 70, 71, 75, 78, 79, 81, 82, 83, 84, 87, 89, 92, 101, 102, 103, 105, 106, 110, 113, 114, 115, 116, 118, 119, 121, 123, 130, 133, 134, 136, 137, 139, 140, 147, 149, 151, 152, 154, 155, 156, 162, 163, 164, 166, 169, 170, 171, 173, 174, 177, 178, 179, 180, 182, 184, 185, 186, 187, 188, 189, 190, 192, 193, 197, 198, 199, 200, 202, 203, 204, 205, 208, 209, 210, 211, 21

Первоначальное представление о датасете:

- Датасет содержит 14456 строк и 2666 колонок. Количество колонок достаточно большое, так что в основном нужно будет работать с ними, даже не зная какие именно данные они представляют.
- Судя по уникальным значениям в каждой колонке, несколько колонок содержат одинаковые или почти одинаковые значения. Из этого можно сделать вывод, что несколько колонок могут представлять из себя один признак, разделенный на несколько колонок. Скорее всего стоит обьединить колонки с одинаковыми уникальными значениями в одну.
- Из задания известно, что в столбце "client_id" представлены уникальные идентификаторы клиентов, а также что каждому клиенту в датасете может быть представлено несколько срезов за разные даты. Таким образом данные об одних и тех же клиентах могут повторяться, что может значительно повлиять на данные. Возможно из одинаковых записей про клиента стоит взять только последнюю.
- Также можно заметить, что некоторые колонки содержат только значения Nan и/или 0. Эти колонки могут быть удалены из датасета, так как они не несут полезной информации.

# Удаление колонок с только нулями и NaN-значениями

In [5]:
for column in df.columns:
    unique_values = df[column].dropna().unique()
    if set(unique_values).issubset({0}):
        print(f"Колонка '{column}' содержит только значения NaN и 0.")

Колонка 'col773' содержит только значения NaN и 0.
Колонка 'col774' содержит только значения NaN и 0.
Колонка 'col775' содержит только значения NaN и 0.
Колонка 'col776' содержит только значения NaN и 0.
Колонка 'col777' содержит только значения NaN и 0.
Колонка 'col778' содержит только значения NaN и 0.
Колонка 'col779' содержит только значения NaN и 0.
Колонка 'col780' содержит только значения NaN и 0.
Колонка 'col781' содержит только значения NaN и 0.
Колонка 'col782' содержит только значения NaN и 0.
Колонка 'col783' содержит только значения NaN и 0.
Колонка 'col784' содержит только значения NaN и 0.
Колонка 'col785' содержит только значения NaN и 0.
Колонка 'col786' содержит только значения NaN и 0.
Колонка 'col787' содержит только значения NaN и 0.
Колонка 'col788' содержит только значения NaN и 0.
Колонка 'col789' содержит только значения NaN и 0.
Колонка 'col790' содержит только значения NaN и 0.
Колонка 'col791' содержит только значения NaN и 0.
Колонка 'col792' содержит тольк

In [6]:
# код чтобы убрать все колонки, в которых есть только нули и NaN-значения - скорее всего убрать, так как нули тоже могут быть полезными значениями
# columns_to_remove = []

# for column in df.columns:
#     unique_values = df[column].dropna().unique()
#     if set(unique_values).issubset({0}):
#         columns_to_remove.append(column)

# df.drop(columns=columns_to_remove, inplace=True)

# # Print the list and count of removed columns
# print(f"Удаленные колонки: {columns_to_remove}")
# print(f"Количество удаленных колонок: {len(columns_to_remove)}")


In [7]:
df.info()

<class 'pandas.core.frame.DataFrame'>
RangeIndex: 14456 entries, 0 to 14455
Columns: 2666 entries, report_date to col2663
dtypes: float64(2316), int64(3), object(347)
memory usage: 294.0+ MB


In [8]:
null_counts = df.isnull().sum()
print(null_counts)

report_date        0
client_id          0
target             0
col1           14453
col2           14450
               ...  
col2659        13950
col2660         6420
col2661         6420
col2662         6420
col2663            0
Length: 2666, dtype: int64


In [ ]:
# для работы с повторяющимися срезами по одному клиенту
df["client_id"].value_counts()


client_id
50      12
49      11
806     11
663     11
615     11
        ..
7711     1
4697     1
8274     1
1856     1
7627     1
Name: count, Length: 4817, dtype: int64

# (Попытки) Вычисление, какие колонки могут представлять из себя один признак, разделенный на несколько колонок.

In [10]:
from sklearn.preprocessing import OrdinalEncoder

# categorical_columns = df_filled.select_dtypes(include=['object']).columns.tolist()
# ordinal_encoder = OrdinalEncoder()
# encoded_data = ordinal_encoder.fit_transform(df[categorical_columns])
# df_filled[categorical_columns] = encoded_data.astype(int)

In [11]:
# plt.figure(figsize=(12, 8))
# sns.heatmap(df_filled.corr(), annot=True, cmap="Blues")
# plt.show()

In [12]:
df_filled = df.fillna(0)

categorical_columns = df_filled.select_dtypes(include=['object']).columns.tolist()

df_filled[categorical_columns] = df_filled[categorical_columns].astype(str)

ordinal_encoder = OrdinalEncoder()
encoded_data = ordinal_encoder.fit_transform(df_filled[categorical_columns])
df_filled[categorical_columns] = encoded_data.astype(int)

In [ ]:
plt.figure(figsize=(12, 8))
sns.heatmap(df_filled.corr(), annot=True, cmap="Blues")
plt.show()